# Daten analysieren

Zufallszahlen und Sinuswerte zu visualisieren ist ganz nett, in der Realtität müssen aber Ergebnisse aus Umfragen oder Messwerte von Experimenten ausgewertet werden.

Standard für die Datenanlyse mit Python ist das Package `pandas`.

In [4]:
import pandas

Um zu demonstrieren, wie `pandas` funktioniert, brauchen wir ein paar Daten. Die finden wir in der Datei `car.csv`, in der die Kosten eines Autos über mehrere Jahre hinweg erfasst wurden.

CSV (Comma Separated Values) gibt es in verschiedenen Ausprägungen. In unserer Datei sind die Daten nicht mit Komma sondern einem Tabulator voneinander getrennt. Das muss man beim Einlesen mit `sep="\t"` angeben.

## Hinweis

Bei den folgenden Beispielen wird die Datei `car.csv` benötigt.
Diese findet sich [hier](https://gist.githubusercontent.com/cgiess/58f995bf88cd0e2269b634c7970eb479/raw/2de29b036ead1eabc402301e934b82e8f674aaf4/car.csv). Diese Datei muss auf den Jupyter-Rechner liegen. In der Regel kann man dies mittels `Upload Files` erreichen.

![upload_file.png](upload_file.png)


Das `Upload Files` funktioniert aber bei https://jupyter.org/try-jupyter/lab/ nicht. Hier muss die Datei wie folgt bereitsgestellt werden (Stand Mai 2022):


```
from js import fetch
res = await fetch('https://gist.githubusercontent.com/cgiess/58f995bf88cd0e2269b634c7970eb479/raw/2de29b036ead1eabc402301e934b82e8f674aaf4/car.csv')
text = await res.text()
with open('car.csv', 'w') as f:
   f.write(text)

import os
os.listdir()
```

Als Ergebnis sollte eine Liste mit Dateienamen angezeigt werden in der `car.csv` enthalten ist, z.B.:

`['.matplotlib', '.ipython', 'car.csv']`

## CSV Dateien mit Pandas lesen

In [5]:
d = pandas.read_csv("file:car.csv", sep="\t")
d

Datum      Typ Beschreibung     Preis      km  Liter
0    2012-07-07     Kauf     Autohaus  13800.00      30    NaN
1    2012-07-10   Benzin         ESSO     57.01     199  34.89
2    2012-07-11  Versich     Haftpfl.    104.30     400    NaN
3    2012-07-23   Benzin     Kaufland     55.03     828  34.20
4    2012-08-10   Benzin     Kaufland     56.72    1444  35.47
..          ...      ...          ...       ...     ...    ...
227  2021-08-28   Benzin         AVIA     47.10  104552  29.27
228  2021-10-09   Benzin     Kaufland     55.10  105147  33.97
229  2021-10-19   Benzin          JET     40.10  105623  24.32
230  2021-12-04   Benzin          JET     53.30  106186  34.19
231  2021-12-25   Benzin         AVIA     51.42  106727  31.96

[232 rows x 6 columns]

Das scheint funktioniert zu haben. Eine kleine Änderung werden wir noch vornehmen. Die erste Spalte enthält ein Datum. Da dies verschieden geschrieben werden kann (31.12.2020, 12/31/2020, ...) müssen wir bei der Erkennung ein bisschen nachhelfen. In unserem Fall ist es ausreichend zu sagen, welche Spalten ein Datum enthalten.

In [6]:
d = pandas.read_csv('file:car.csv', sep='\t', parse_dates=['Datum'])

## Auf einzelne Daten zugreifen

Der Rückgabewert von `read_csv` ist ein **Data Frame**.
Das sieht aus wie eine Tabelle. Was kann man damit nun machen?

In [7]:
d["Preis"]

0      13800.00
1         57.01
2        104.30
3         55.03
4         56.72
         ...   
227       47.10
228       55.10
229       40.10
230       53.30
231       51.42
Name: Preis, Length: 232, dtype: float64

Einzelne Spalten kann man über den Spaltentitel adressieren. So eine Spalte nennt Pandas **Series**.
Möchte man einen Wert aus so einer Series haben, so muss man zusätzlich dessen Zeilennummer angeben.

In [8]:
d["Preis"][0]

13800.0

Das Ganze geht auch umgekehrt.
Eine Zeile bekommt man über den Array `iloc`:

In [9]:
d.iloc[0]

Datum           2012-07-07 00:00:00
Typ                            Kauf
Beschreibung               Autohaus
Preis                       13800.0
km                               30
Liter                           NaN
Name: 0, dtype: object

... und einen einzelnen Wert daraus über den Spaltennamen.

In [24]:
d.iloc[0]["km"]

30

Mit `head()` und `tail()` kann man zudem die ersten bzw. letzten N Spalten auswählen.

In [11]:
d.head(2).tail(1)

Datum     Typ Beschreibung  Preis   km  Liter
1 2012-07-10  Benzin         ESSO  57.01  199  34.89

## Aufgabe
Wie bekommt man die 4. bis 6. Zeile?

## Lösung
Achtung: die 4. Zeile hat die Nummer 3 weil die Nummerierung mit 0 beginnt!

In [12]:
d.head(6).tail(3)

Datum      Typ Beschreibung  Preis    km  Liter
3 2012-07-23   Benzin     Kaufland  55.03   828  34.20
4 2012-08-10   Benzin     Kaufland  56.72  1444  35.47
5 2012-08-23  Steuern   Kfz-Steuer  50.00  1500    NaN

## Was wissen die Daten über sich selbst?
Der Data Frame kann über sich selbst etwas sagen:

In [13]:
d.dtypes

Datum           datetime64[ns]
Typ                     object
Beschreibung            object
Preis                  float64
km                       int64
Liter                  float64
dtype: object

Was bedeutet dies?
Für jede Spalte wird angegeben, welchen Typ die darin enthaltenen Daten besitzen.
* datetime64\[ns] - ist ein Zeitstempel bestehend aus Datum und Uhrzeit wobei letztere eine Genauigkeit von Nanosekunden hat
* object - das sind Texte
* float64 - Zahl mit Nachkommastellen.
* int64 - Zahl ohne Nachkommastellen

Über die Verteilung der Zahlen gibt die Funktion `describe()` Auskunft.

In [14]:
d.describe()

Preis             km       Liter
count    232.000000     232.000000  201.000000
mean     117.583578   53910.508621   31.144726
std      904.538671   31374.136420    4.261039
min        0.000000      30.000000   10.140000
25%       39.840000   27386.750000   29.890000
50%       45.160000   53140.000000   32.640000
75%       50.000000   81382.000000   33.650000
max    13800.000000  106727.000000   37.930000

## Aufgabe

1. Welche Bedeutung haben diese Zahlen?
1. Welche davon helfen beim Verständnis der Daten?
1. Gibt es Datensätze, wo diese Funktion noch viel hilfreicher ist?

## Lösung
Die besprechen wir im Kurs

## Zeilen zählen

In [15]:
d.count()

Datum           232
Typ             232
Beschreibung    232
Preis           232
km              232
Liter           201
dtype: int64

In der Spalte **Liter** fehlen einige Einträge. Darum liefert `count()` für diese einen kleineren Wert.
Nicht vorhandene Werte werden als **NaN** (Not a Number) angezeigt.

## Werte zählen

In [16]:
d["Typ"].value_counts()

Benzin     201
Versich     10
Steuern     10
Werkst       9
Kauf         2
Name: Typ, dtype: int64

## Rechnen

Welche Kosten sind insgesamt angefallen? Dazu muss man alle Einträge der Spalte `Preis` aufsummieren.

In [17]:
d["Preis"].sum()

27279.390000000003

## Aufgabe

Was ist der Durchschnittsverbrauch des Autos über die gesamte erfasste Zeit?

**Hinweise**
* Gesamtverbrauch, d.h. wieviele Liter wurden insgesamt verbraucht
* Fahrstrecke, d.h. km-Stand am Ende - km-Stand am Anfang
* Verbrauch wird i.d.R. in l/100km angegeben

## Lösung

In [28]:
l_total  = d["Liter"].sum()

km_start = d["km"].min() # oder d["km"][0] -> km-Stand aus der 0ten Zeile
km_end   = d["km"].max()   # oder d["km"].iloc[-1] -> km-Stand aus der letzten Zeile,
                         # geht man von 0 eins zurück fängt man am Ende wieder an

km_total = km_end - km_start

fuel_avg = 100 * l_total / km_total
fuel_avg

5.867165899697274

## Daten filtern
Wenn man nur an einem Teil der Daten interessiert ist kann man sich diesen selektieren.

In [19]:
fuel_only = d[d["Typ"] == "Benzin"]
fuel_only.head(2)

Datum     Typ Beschreibung  Preis   km  Liter
1 2012-07-10  Benzin         ESSO  57.01  199  34.89
3 2012-07-23  Benzin     Kaufland  55.03  828  34.20

## Aufgabe
1. Selektiere die Zeilen, bei denen der Preis kleiner als 100 ist.
1. Selektiere die Zeilen, bei denen der Preis gleich 50 ist.
1. Selektiere die Zeilen, bei denen Liter größer 36 und kleiner 38 sind.

## Lösung

In [20]:
d[d["Preis"] < 100]
d[d["Preis"] == 50]
# d.described() sagte, dass der größte Wert 37.93 ist
d[d["Liter"] > 36]
d[d["Liter"].between(36,38)]

Datum     Typ Beschreibung  Preis     km  Liter
6   2012-09-10  Benzin         AVIA  60.80   2061  36.87
7   2012-09-14  Benzin          OMV  61.10   2710  36.83
106 2016-09-15  Benzin     Kaufland  48.51  48872  37.93
124 2017-05-30  Benzin         Real  46.78  57868  36.01

## Daten Gruppieren

Die Kosten sollen nach Spalte `Typ` bzw `Beschreibung` aufsummiert werden.

In [21]:
d.groupby("Typ")["Preis"].sum()

Typ
Benzin      8704.15
Kauf       14296.68
Steuern      500.00
Versich     2596.02
Werkst      1182.54
Name: Preis, dtype: float64

In [22]:
fuel_only.groupby("Beschreibung")["Preis"].sum()

Beschreibung
AGIP            32.80
ARAL           795.33
AVIA           671.59
Autohof         45.30
Avanti          64.10
BFT             88.66
BP              46.05
Bavaria         44.00
ESSO          1320.52
Elf             45.00
Globus         798.94
HEM             27.70
JET           1074.80
KK             183.34
Kaufland      1080.48
OMV             95.38
Oil            261.71
Real           222.15
SHELL          539.30
Star            99.80
Tango           56.85
Tankcenter     413.43
Total          481.25
UNO-X           43.36
Unbekannt      172.31
Name: Preis, dtype: float64

Das ist doch nett. Noch schöner wäre aber, wenn die Daten nach der zweiten Spalte absteigend sortiert wären.
Zudem ist man oft nur an den größten Ergebnissen interessiert.

In [29]:
fuel_only.groupby("Beschreibung")["Preis"].sum().sort_values(ascending=False).head(10)

Beschreibung
ESSO          1320.52
Kaufland      1080.48
JET           1074.80
Globus         798.94
ARAL           795.33
AVIA           671.59
SHELL          539.30
Total          481.25
Tankcenter     413.43
Oil            261.71
Name: Preis, dtype: float64